In [1]:
import os
import sys
import numpy as np
import pandas as pd
pd.set_option('display.max_columns', 50)

from matplotlib import pyplot as plt
import seaborn as sns
%matplotlib inline

import plotly
import plotly.graph_objs as go
import cufflinks as cf
cf.set_config_file(offline=True)

In [2]:
base_path = os.path.abspath('../..')
data_path = os.path.join(base_path, 'data')
database_path = os.path.join(data_path, 'database')
strategy_path = os.path.join(base_path, 'strategy')
check_path = os.path.join(strategy_path, 'check')
r_signal_path = os.path.join(check_path, 'signal')
sys.path.append(strategy_path)

In [3]:
from strategy import CommodityStrategy, EquityStrategy, IRStrategy, EmergingStrategy
from tester import Tester

In [4]:
from EMDY import EMDY
from EMPE import EMPE
from EMPM import EMPM
from EMSS import EMSS
from EMCA import EMCA
#from EMVO import EMVO

In [5]:
# EM equity data
emindex = pd.read_csv(os.path.join(data_path, 'totindex-em.csv'), header=0, index_col=0, parse_dates=True)
emindex1 = pd.read_csv(os.path.join(data_path, 'priceindex-em.csv'), header=0, index_col=0, parse_dates=True)
emfut = pd.read_csv(os.path.join(data_path, 'fut1return-em.CSV'), header=0, index_col=0, parse_dates=True)

total_em_ret = emindex.pct_change()
prc_em_ret = emindex1.pct_change()
fut_em_ret = emfut.pct_change()
fut_em_ret = fut_em_ret.reindex(pd.date_range(fut_em_ret.index[0], fut_em_ret.index[-1], freq ='B')) # bizday로 변환

prc_em_ret.loc[total_em_ret.index] = total_em_ret
raw_index = pd.concat([emindex1.loc[:'2012-12-31'], emfut.loc['2013-01-01':]]).iloc[1:]
EMRet = pd.concat([prc_em_ret.loc[:'2012-12-31'], fut_em_ret.loc['2013-01-01':]]).iloc[1:]

EMRet.fillna(0, inplace = True)
EMindex = EMRet
EMindex.iloc[0] = 0
EMindex = (1+ EMindex).cumprod()
EMindex = EMindex / EMindex.iloc[0]

raw_index.index.name = 'tdate'
raw_index.columns.name = 'ticker'

EMindex.index.name = 'tdate'
EMRet.index.name = 'tdate'

EMindex.columns.name = 'ticker'
EMRet.columns.name = 'ticker'

raw_index = pd.read_csv(os.path.join(data_path,'priceindex-mon-em.csv') ,header=0, index_col=0, parse_dates=True)
raw_index.index.name = 'tdate'
raw_index.columns.name = 'ticker'

# 1. EMDY

In [6]:
raw_index

ticker            CN        KR        TW         IN        MY         ID  \
tdate                                                                      
1994-12-30   70.5330  181.3790  300.8270   147.6680  342.1419   629.8550   
1995-01-31   60.7890  164.9380  263.9440   138.5510  307.8126   581.1350   
1995-02-28   67.7300  161.4700  272.6890   131.4340  348.7829   629.6160   
1995-03-31   67.8430  171.0610  271.1190   126.4120  346.7121   601.1050   
1995-04-28   60.6080  169.1260  241.8710   120.0890  333.7535   572.9360   
...              ...       ...       ...        ...       ...        ...   
2017-11-30   87.3277  746.8345  391.9208  1218.5909  597.8897  6905.1605   
2017-12-29   89.0496  748.7678  393.4431  1265.1442  625.4306  7518.2545   
2018-01-31  100.2063  773.5789  414.6132  1303.5538  649.0757  7642.1652   
2018-02-28   93.8201  732.9909  402.7700  1243.5714  642.3855  7609.1496   
2018-03-30   90.9301  738.3918  407.4249  1198.2329  643.6499  7058.9332   

ticker                BR          MX         RU         SA  
tdate                                                       
1994-12-30  2.395458e+10   2566.3650   100.0000   181.7140  
1995-01-31  2.168688e+10   2302.0470    78.0130   156.0070  
1995-02-28  1.854676e+10   1821.4140    62.4290   159.7170  
1995-03-31  1.701694e+10   2109.3240    67.8170   165.4660  
1995-04-28  2.070906e+10   2186.9240    51.3220   171.2080  
...                  ...         ...        ...        ...  
2017-11-30  2.440268e+11  44350.3393   946.9652  1557.7649  
2017-12-29  2.573139e+11  46586.1487   955.1222  1537.4784  
2018-01-31  2.867972e+11  47707.7306  1053.9486  1514.6085  
2018-02-28  2.861185e+11  44920.2749  1064.3235  1501.7325  
2018-03-30  2.866769e+11  43763.8722  1043.3542  1401.9185  

[280 rows x 10 columns]

In [7]:
strategy_name = 'EMDY'
emdy = EMDY(strategy_name = strategy_name, asset_type="EMERGING")
# 필요 데이터 생성
DPS = pd.read_csv(os.path.join(data_path,'DPS-em.csv') ,header=0, index_col=0, parse_dates=True)
DPS1 = pd.read_csv(os.path.join(data_path,'DPS1-em.csv') ,header=0, index_col=0, parse_dates=True)
yield_ = pd.read_csv(os.path.join(data_path,'10Yield-em.csv') ,header=0, index_col=0, parse_dates=True)
#필요 데이터 넣기 
emdy.index = EMindex.copy()
emdy.ret = EMRet.copy()
emdy.dps = DPS
emdy.dps1 = DPS1
emdy.yield10 = yield_
emdy.raw_index = raw_index

emdy.calculate_signal()
CSRV = emdy.CSRV
TSRV = emdy.TSRV
# R signal과 비교
R_TSRV =  pd.read_csv(os.path.join(r_signal_path, f'{strategy_name}_TSRV.csv'),
                      index_col = 'Unnamed: 0')

(R_TSRV- TSRV).abs().sum(1).iplot()

R_CSRV =  pd.read_csv(os.path.join(r_signal_path, f'{strategy_name}_CSRV.csv'),
                      index_col = 'Unnamed: 0')

(R_CSRV- CSRV).abs().sum(1).iplot()

emdy.set_rebalance_period(ts_freq='month', cs_freq='month')
emdy.set_portfolio_parameter(cs_strategy_type='notional')
emdy.make_portfolio()

2020-01-02 10:39:01,953 - EMDY - INFO - [STEP 0] START LOGGING EMDY
C:\Users\jungyoon.choi\Desktop\jungyoon\project\risk_premia\python\strategy\EMDY.py:72: FutureWarning:


Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#deprecate-loc-reindex-listlike

C:\Users\jungyoon.choi\Desktop\jungyoon\project\risk_premia\python\strategy\EMDY.py:73: FutureWarning:


Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#deprecate-loc-reindex-listlike



2020-01-02 10:39:03,740 - EMDY - INFO - [STEP 2] SET REBALANCE PERIOD
2020-01-02 10:39:03,741 - EMDY - INFO - [STEP 4] SET PORTFOLIO PARAMETER
2020-01-02 10:39:03,741 - EMDY - INFO - [STEP 5] MAKE PORTFOLIO
2020-01-02 10:39:03,742 - EMDY - INFO - [STEP 5 - 1] CALCULATE VOLATILITY
2020-01-02 10:39:33,568 - EMDY - INFO - [STEP 5 - 2] MAKE TS POSITION
2020-01-02 10:39:33,569 - EMDY - INFO - [STEP 5 - 2 - 1] ALIGN TS POSITION WITH REBALANCE DAY
2020-01-02 10:39:34,877 - EMDY - INFO - [STEP 5 - 2 - 2] TARGET VOL CONTROL to TS POSITION
2020-01-02 10:39:34,882 - EMDY - INFO - [STEP 5 - 2 - 3] STRATEGY LEVEL VOL CONTROL to TS POSITION
2020-01-02 10:39:35,429 - EMDY - INFO - [STEP 5 - 2 - 4] MAKE FINAL TS POSITION
2020-01-02 10:39:35,432 - EMDY - INFO - [STEP 5 - 3] MAKE CS POSITION
2020-01-02 10:39:35,432 - EMDY - INFO - [STEP 5 - 3 - 1] NO TARGET VOL CONTROL to CS POSITION
2020-01-02 10:39:35,433 - EMDY - INFO - [STEP 5 - 3 - 2] ALIGN CS POSITION WITH REBALANCE DAY
2020-01-02 10:39:37,543 - E

In [8]:
start_date = '2006-01-01'
end_date = '2018-05-09'

# get r results
emdy_comp_df = pd.read_csv('./past/emdy.csv', header=0, index_col=0, parse_dates=True)
emdy_lag_comp_df = pd.read_csv('./past/emdy_lag.csv', header=0, index_col=0, parse_dates=True)

In [9]:
tester = Tester(emdy)
tester.set_period(start=start_date, end=end_date)
tester.run(save_file=False)

2020-01-02 10:39:38,286 - EMDY - INFO - [STEP 6] START BACKTEST
2020-01-02 10:39:38,287 - EMDY - INFO - [STEP 6 - 1] BACKTEST EMDY TIME SERIES
2020-01-02 10:39:38,939 - EMDY - INFO - [STEP 6 - 2] BACKTEST EMDY CROSS SECTIONAL


In [10]:
to_plot = (1.+ emdy_lag_comp_df).loc[start_date:].cumprod()
to_plot['TS_python'] = tester.strategy.TS_result
to_plot['CS_python'] = tester.strategy.CS_result
to_plot.iplot()

# 2. EMPE

In [11]:
strategy_name = 'EMPE'
empe = EMPE(strategy_name=strategy_name, asset_type="EMERGING")
empe.index = EMindex.copy()
empe.ret = EMRet.copy()

# empe.load_index_and_return(from_db=False, save_file=False)
# empe.load_strategy_data1(table='DS', origin1='EPS-em', origin2='EPS1-em')
# empe.load_strategy_data2(table='bloom', origin='10Yield-em')

# 필요 데이터 : eps, eps1, yield10, raw_index
eps = pd.read_csv(os.path.join(data_path, "EPS-em.csv"), index_col=0, parse_dates=True)
eps.index.name = 'tdate'
eps.columns.name = 'ticker'

eps1 = pd.read_csv(os.path.join(data_path, "EPS1-em.csv"), index_col=0, parse_dates=True)
eps1.index.name = 'tdate'
eps1.columns.name = 'ticker'

yield10 = pd.read_csv(os.path.join(data_path, '10Yield-em.csv'), index_col=0, parse_dates=True)
yield10.index.name = 'tdate'
yield10.columns.name = 'ticker'

empe.eps = eps
empe.eps1 = eps1
empe.yield10 = yield10
empe.raw_index = raw_index

empe.set_rebalance_period(cs_freq='month', ts_freq='month')
empe.calculate_signal(CS=0.35, nopos=0.4, minobs1=12, minobs=60, IDN='out')
CSRV = empe.CSRV
TSRV = empe.TSRV
# R signal과 비교
R_TSRV =  pd.read_csv(os.path.join(r_signal_path, f'{strategy_name}_TSRV.csv'),
                      index_col = 'Unnamed: 0')
R_TSRV.index = pd.to_datetime(R_TSRV.index)
np.round((R_TSRV- TSRV).abs(), 4).sum(1).iplot(title = 'TS')

R_CSRV =  pd.read_csv(os.path.join(r_signal_path, f'{strategy_name}_CSRV.csv'),
                      index_col = 'Unnamed: 0')
R_CSRV.index = pd.to_datetime(R_CSRV.index)
np.round((R_CSRV- CSRV).abs(), 4).sum(1).iplot(title = 'CS')

empe.set_portfolio_parameter(cs_strategy_type='notional')
empe.make_portfolio()

2020-01-02 10:39:40,886 - EMPE - INFO - [STEP 0] START LOGGING EMPE
2020-01-02 10:39:40,894 - EMPE - INFO - [STEP 2] SET REBALANCE PERIOD
C:\Users\jungyoon.choi\Desktop\jungyoon\project\risk_premia\python\strategy\EMPE.py:63: FutureWarning:


Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#deprecate-loc-reindex-listlike

C:\Users\jungyoon.choi\Desktop\jungyoon\project\risk_premia\python\strategy\EMPE.py:64: FutureWarning:


Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#deprecate-loc-reindex-listlike



2020-01-02 10:39:43,635 - EMPE - INFO - [STEP 4] SET PORTFOLIO PARAMETER
2020-01-02 10:39:43,636 - EMPE - INFO - [STEP 5] MAKE PORTFOLIO
2020-01-02 10:39:43,636 - EMPE - INFO - [STEP 5 - 1] CALCULATE VOLATILITY
2020-01-02 10:40:14,207 - EMPE - INFO - [STEP 5 - 2] MAKE TS POSITION
2020-01-02 10:40:14,208 - EMPE - INFO - [STEP 5 - 2 - 1] ALIGN TS POSITION WITH REBALANCE DAY
2020-01-02 10:40:16,412 - EMPE - INFO - [STEP 5 - 2 - 2] TARGET VOL CONTROL to TS POSITION
2020-01-02 10:40:16,418 - EMPE - INFO - [STEP 5 - 2 - 3] STRATEGY LEVEL VOL CONTROL to TS POSITION
2020-01-02 10:40:17,284 - EMPE - INFO - [STEP 5 - 2 - 4] MAKE FINAL TS POSITION
2020-01-02 10:40:17,287 - EMPE - INFO - [STEP 5 - 3] MAKE CS POSITION
2020-01-02 10:40:17,288 - EMPE - INFO - [STEP 5 - 3 - 1] NO TARGET VOL CONTROL to CS POSITION
2020-01-02 10:40:17,288 - EMPE - INFO - [STEP 5 - 3 - 2] ALIGN CS POSITION WITH REBALANCE DAY
2020-01-02 10:40:20,705 - EMPE - INFO - [STEP 5 - 3 - 3] STRATEGY LEVEL VOL CONTROL to CS POSITIO

In [12]:
start_date = '2001-01-01'
end_date = '2018-05-09'

# get r results
empe_comp_df = pd.read_csv('./past/empe.csv', header=0, index_col=0, parse_dates=True)
empe_lag_comp_df = pd.read_csv('./past/empe_lag.csv', header=0, index_col=0, parse_dates=True)

In [13]:
tester = Tester(empe)
tester.set_period(start=start_date, end=end_date)
tester.run(save_file=False)

2020-01-02 10:40:21,939 - EMPE - INFO - [STEP 6] START BACKTEST
2020-01-02 10:40:21,939 - EMPE - INFO - [STEP 6 - 1] BACKTEST EMPE TIME SERIES
2020-01-02 10:40:22,974 - EMPE - INFO - [STEP 6 - 2] BACKTEST EMPE CROSS SECTIONAL


In [14]:
to_plot = (1.+ empe_lag_comp_df).loc[start_date:].cumprod()
to_plot['TS_python'] = tester.strategy.TS_result
to_plot['CS_python'] = tester.strategy.CS_result
to_plot.iplot()

# 3. EMPM

In [16]:
strategy_name = "EMPM"
empm = EMPM(strategy_name=strategy_name, asset_type="EMERGING")
empm.index = EMindex.copy()
empm.ret = EMRet.copy()

empm.set_rebalance_period(ts_freq='month', cs_freq='week', rebalance_weekday=1)  # rebalance_day: monday = 0, sunday = 6
empm.calculate_signal(CS=0.35, minobs=260, minobs1=52, longlen1=52, longlen2=13, shortlen=2)

CSRV = empm.CSRV
TSRV = empm.TSRV

# R signal과 비교
R_TSRV =  pd.read_csv(os.path.join(r_signal_path, f'{strategy_name}_TSRV.csv'),
                      index_col = 'Unnamed: 0')
R_TSRV.index = pd.to_datetime(R_TSRV.index)
np.round((R_TSRV- TSRV).abs(), 4).sum(1).iplot(title = 'TS')

R_CSRV =  pd.read_csv(os.path.join(r_signal_path, f'{strategy_name}_CSRV.csv'),
                      index_col = 'Unnamed: 0')
R_CSRV.index = pd.to_datetime(R_CSRV.index)
np.round((R_CSRV- CSRV).abs(), 4).sum(1).iplot(title = 'CS')

empm.set_portfolio_parameter(cs_strategy_type='notional')
empm.make_portfolio()

2020-01-02 10:40:34,738 - EMPM - INFO - [STEP 0] START LOGGING EMPM
2020-01-02 10:40:34,738 - EMPM - INFO - [STEP 0] START LOGGING EMPM
2020-01-02 10:40:34,739 - EMPM - INFO - [STEP 2] SET REBALANCE PERIOD
2020-01-02 10:40:34,739 - EMPM - INFO - [STEP 2] SET REBALANCE PERIOD
C:\Users\jungyoon.choi\Desktop\jungyoon\project\risk_premia\python\strategy\EMPM.py:70: FutureWarning:


Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#deprecate-loc-reindex-listlike

C:\Users\jungyoon.choi\Desktop\jungyoon\project\risk_premia\python\strategy\EMPM.py:71: FutureWarning:


Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#deprecate-loc-rein

2020-01-02 10:40:38,897 - EMPM - INFO - [STEP 4] SET PORTFOLIO PARAMETER
2020-01-02 10:40:38,897 - EMPM - INFO - [STEP 4] SET PORTFOLIO PARAMETER
2020-01-02 10:40:38,898 - EMPM - INFO - [STEP 5] MAKE PORTFOLIO
2020-01-02 10:40:38,898 - EMPM - INFO - [STEP 5] MAKE PORTFOLIO
2020-01-02 10:40:38,898 - EMPM - INFO - [STEP 5 - 1] CALCULATE VOLATILITY
2020-01-02 10:40:38,898 - EMPM - INFO - [STEP 5 - 1] CALCULATE VOLATILITY
2020-01-02 10:41:09,892 - EMPM - INFO - [STEP 5 - 2] MAKE TS POSITION
2020-01-02 10:41:09,892 - EMPM - INFO - [STEP 5 - 2] MAKE TS POSITION
2020-01-02 10:41:09,893 - EMPM - INFO - [STEP 5 - 2 - 1] ALIGN TS POSITION WITH REBALANCE DAY
2020-01-02 10:41:09,893 - EMPM - INFO - [STEP 5 - 2 - 1] ALIGN TS POSITION WITH REBALANCE DAY
2020-01-02 10:41:11,991 - EMPM - INFO - [STEP 5 - 2 - 2] TARGET VOL CONTROL to TS POSITION
2020-01-02 10:41:11,991 - EMPM - INFO - [STEP 5 - 2 - 2] TARGET VOL CONTROL to TS POSITION
2020-01-02 10:41:11,997 - EMPM - INFO - [STEP 5 - 2 - 3] STRATEGY LE

In [17]:
start_date = '2001-01-01'
end_date = '2018-05-09'

# get r results
empm_comp_df = pd.read_csv('./past/empm.csv', header=0, index_col=0, parse_dates=True)
empm_lag_comp_df = pd.read_csv('./past/empm_lag.csv', header=0, index_col=0, parse_dates=True)

In [18]:
tester = Tester(empm)
tester.set_period(start=start_date, end=end_date)
tester.run(save_file=False)

2020-01-02 10:41:20,417 - EMPM - INFO - [STEP 6] START BACKTEST
2020-01-02 10:41:20,417 - EMPM - INFO - [STEP 6] START BACKTEST
2020-01-02 10:41:20,418 - EMPM - INFO - [STEP 6 - 1] BACKTEST EMPM TIME SERIES
2020-01-02 10:41:20,418 - EMPM - INFO - [STEP 6 - 1] BACKTEST EMPM TIME SERIES
2020-01-02 10:41:21,828 - EMPM - INFO - [STEP 6 - 2] BACKTEST EMPM CROSS SECTIONAL
2020-01-02 10:41:21,828 - EMPM - INFO - [STEP 6 - 2] BACKTEST EMPM CROSS SECTIONAL


In [19]:
to_plot = (1.+ empm_lag_comp_df).loc[start_date:].cumprod()
to_plot['TS_python'] = tester.strategy.TS_result
to_plot['CS_python'] = tester.strategy.CS_result
to_plot.iplot()

# 4. EMSS

In [20]:
emss = EMSS(strategy_name="EMSS", asset_type="EMERGING")
emss.index = EMindex.copy()
emss.ret = EMRet.copy()

# emss.load_index_and_return(from_db=False, save_file=False)
emss.set_rebalance_period(ts_freq='month', cs_freq='month')  # rebalance_day: monday = 0, sunday = 6
emss.calculate_signal(CS=0.35, short=0.2, day1=24, fundwgt=1, statwgt=1)

2020-01-02 10:41:24,666 - EMSS - INFO - [STEP 0] START LOGGING EMSS
2020-01-02 10:41:24,667 - EMSS - INFO - [STEP 2] SET REBALANCE PERIOD


In [21]:
emss.TSRV.fillna(0, inplace=True)
emss.CSRV.fillna(0, inplace=True)

In [22]:
emss.set_portfolio_parameter(cs_strategy_type="notional")
emss.make_portfolio()

2020-01-02 10:42:30,458 - EMSS - INFO - [STEP 4] SET PORTFOLIO PARAMETER
2020-01-02 10:42:30,459 - EMSS - INFO - [STEP 5] MAKE PORTFOLIO
2020-01-02 10:42:30,459 - EMSS - INFO - [STEP 5 - 1] CALCULATE VOLATILITY
2020-01-02 10:43:01,236 - EMSS - INFO - [STEP 5 - 2] MAKE TS POSITION
2020-01-02 10:43:01,237 - EMSS - INFO - [STEP 5 - 2 - 1] ALIGN TS POSITION WITH REBALANCE DAY
2020-01-02 10:43:03,559 - EMSS - INFO - [STEP 5 - 2 - 2] TARGET VOL CONTROL to TS POSITION
2020-01-02 10:43:03,564 - EMSS - INFO - [STEP 5 - 2 - 3] STRATEGY LEVEL VOL CONTROL to TS POSITION
2020-01-02 10:43:04,584 - EMSS - INFO - [STEP 5 - 2 - 4] MAKE FINAL TS POSITION
2020-01-02 10:43:04,586 - EMSS - INFO - [STEP 5 - 3] MAKE CS POSITION
2020-01-02 10:43:04,587 - EMSS - INFO - [STEP 5 - 3 - 1] NO TARGET VOL CONTROL to CS POSITION
2020-01-02 10:43:04,587 - EMSS - INFO - [STEP 5 - 3 - 2] ALIGN CS POSITION WITH REBALANCE DAY
2020-01-02 10:43:08,145 - EMSS - INFO - [STEP 5 - 3 - 3] STRATEGY LEVEL VOL CONTROL to CS POSITIO

In [23]:
start_date = '2001-01-01'
end_date = '2018-05-09'

# get r results
emss_comp_df = pd.read_csv('./past/emss.csv', header=0, index_col=0, parse_dates=True)
emss_lag_comp_df = pd.read_csv('./past/emss_lag.csv', header=0, index_col=0, parse_dates=True)

In [24]:
tester = Tester(emss)
tester.set_period(start=start_date, end=end_date)
tester.run(save_file=False)

2020-01-02 10:43:09,284 - EMSS - INFO - [STEP 6] START BACKTEST
2020-01-02 10:43:09,284 - EMSS - INFO - [STEP 6 - 1] BACKTEST EMSS TIME SERIES
2020-01-02 10:43:10,735 - EMSS - INFO - [STEP 6 - 2] BACKTEST EMSS CROSS SECTIONAL


In [25]:
to_plot = (1.+ emss_lag_comp_df).loc[start_date:].cumprod()
to_plot['TS_python'] = tester.strategy.TS_result
to_plot['CS_python'] = tester.strategy.CS_result
to_plot.iplot()

# 5. EMCA

In [26]:
emca = EMCA(strategy_name="EMCA", asset_type="EMERGING")
emca.index = EMindex.copy()
emca.ret = EMRet.copy()

# emca.load_index_and_return(from_db=False, save_file=False)
# emca.load_strategy_data(table='bloom', origin='carry-em')

carry = pd.read_csv(os.path.join(data_path, "carry-em.csv"), index_col=0, parse_dates=True)
carry.index.name = 'tdate'
carry.columns.name = 'ticker'

emca.carry_em = carry

emca.set_rebalance_period(ts_freq='month', cs_freq='month')
emca.calculate_signal(CS=0.5, minobs1=12, nopos=0.4)
emca.set_portfolio_parameter(cs_strategy_type='notional')
emca.make_portfolio()

2020-01-02 10:43:13,364 - EMCA - INFO - [STEP 0] START LOGGING EMCA
2020-01-02 10:43:13,368 - EMCA - INFO - [STEP 2] SET REBALANCE PERIOD
C:\Users\jungyoon.choi\Desktop\jungyoon\project\risk_premia\python\strategy\EMCA.py:37: FutureWarning:


Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#deprecate-loc-reindex-listlike

C:\Users\jungyoon.choi\Desktop\jungyoon\project\risk_premia\python\strategy\EMCA.py:38: FutureWarning:


Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#deprecate-loc-reindex-listlike

2020-01-02 10:43:13,582 - EMCA - INFO - [STEP 4] SET PORTFOLIO PARAMETER
2020-01-02 10:43:13,583 - EMCA - INFO - [STEP 5] MA

In [27]:
start_date = '2001-01-01'
end_date = '2018-05-09'

# get r results
emca_comp_df = pd.read_csv('./past/emca.csv', header=0, index_col=0, parse_dates=True)
emca_lag_comp_df = pd.read_csv('./past/emca_lag.csv', header=0, index_col=0, parse_dates=True)

In [28]:
tester = Tester(emca)
tester.set_period(start=start_date, end=end_date)
tester.run(save_file=False)

2020-01-02 10:43:48,877 - EMCA - INFO - [STEP 6] START BACKTEST
2020-01-02 10:43:48,878 - EMCA - INFO - [STEP 6 - 1] BACKTEST EMCA TIME SERIES
2020-01-02 10:43:49,294 - EMCA - INFO - [STEP 6 - 2] BACKTEST EMCA CROSS SECTIONAL


In [29]:
to_plot = (1.+ emca_lag_comp_df).loc[start_date:].cumprod()
to_plot['TS_python'] = tester.strategy.TS_result
to_plot['CS_python'] = tester.strategy.CS_result
to_plot.iplot()